In [1]:
import numpy as np
import pandas as pd
import QuantLib as ql
import sqlalchemy as db
from scipy import interpolate
from nelson_siegel_svensson.calibrate import calibrate_nss_ols, calibrate_ns_ols

import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.offline


In [2]:
def db_get_yield_curve_data(yield_curve_id, market_date):
    engine = db.create_engine(
        "mssql+pyodbc:///?odbc_connect=Driver={SQL Server};Server=192.168.11.102;Database=IDPM;Trusted_Connection=True;"
    )
    query = f"""select * from YieldCurvePoint yp
    join YieldCurveData yd
        on yd.YieldCurvePointID = yp.YieldCurvePointID
    where yp.YieldCurveID = {yield_curve_id}
    and yd.MarketDate = '{market_date}'"""

    data = pd.read_sql(
        db.text(query),
        engine.connect(),
    )
    return data

def get_forward_rate(data: pd.DataFrame):
    maturity_arr = np.array(data["DaysToMaturity"] / 366)
    yield_arr = np.array(data["Yield"])
    forward_arr = np.zeros(len(yield_arr))
    forward_arr[0] = yield_arr[0]
    for i in range(1, len(yield_arr)):
        forward_arr[i] = (
            yield_arr[i] * maturity_arr[i] - yield_arr[i - 1] * maturity_arr[i - 1]
        ) / (maturity_arr[i] - maturity_arr[i - 1])
    return (forward_arr / 100, maturity_arr)

In [3]:
data = db_get_yield_curve_data(17, '20240515')

In [39]:
data['YearToMaturity'] = data['DaysToMaturity'] / 366
data.head()

YieldCurvePointID  YieldCurveID           RIC  YieldCurveTenorID  \
0                712            17  EURAMMEONZ=R                  1   
1                713            17  EURAMMETNZ=R                  2   
2                714            17  EURAMME1WZ=R                  3   
3                715            17  EURAMME1MZ=R                  4   
4                716            17  EURAMME2MZ=R                  5   

   YieldCurvePointID              MarketDate     Yield  Discount  \
0                712  2024-05-15 00:00:00.00  4.065588  0.999891   
1                713  2024-05-15 00:00:00.00  4.065588  0.999782   
2                714  2024-05-15 00:00:00.00  4.018161  0.999032   
3                715  2024-05-15 00:00:00.00  3.964193  0.996501   
4                716  2024-05-15 00:00:00.00  3.870524  0.993485   

   DaysToMaturity  YearToMaturity  
0               1        0.002732  
1               2        0.005464  
2               9        0.024590  
3              33        0.090164  
4              63        0.172131

In [5]:
yield_arr = np.array(data["Yield"]/100)
y_to_maturity_arr = np.array(data["YearToMaturity"])
new_mat = np.linspace(0, np.ceil(y_to_maturity_arr[-1]), 10000)

yield_fit, _ = calibrate_ns_ols(y_to_maturity_arr, yield_arr)
new_yield = yield_fit(new_mat)

In [6]:
yield_fit_cub_coef = interpolate.CubicSpline(y_to_maturity_arr, yield_arr)
yield_fit_cub = yield_fit_cub_coef(new_mat)

In [7]:
yield_fit_nss, _ = calibrate_nss_ols(y_to_maturity_arr, yield_arr,)
new_yield_nss = yield_fit_nss(new_mat)

In [8]:
dxdyy = np.gradient(yield_arr, y_to_maturity_arr)
yield_fit_hcub_coef = interpolate.CubicHermiteSpline(y_to_maturity_arr, yield_arr, dxdyy, extrapolate=True)
yield_fit_hcub = yield_fit_hcub_coef(new_mat)

In [9]:
forward_rate, maturity = get_forward_rate(data)

In [10]:
forwad_fit, _ = calibrate_nss_ols(maturity, forward_rate)
new_forward = forwad_fit(new_mat)
# forwad_fit_ns, _ = calibrate_ns_ols(maturity, forward_rate)
# new_forward_ns = forwad_fit_ns(new_mat)

In [11]:
# cubic hermite spline
dydxf = np.gradient(forward_rate,y_to_maturity_arr)
forward_fit_hcub_coef = interpolate.CubicHermiteSpline(maturity, forward_rate, dydxf, extrapolate=True)
forward_fit_hcub = forward_fit_hcub_coef(new_mat)

In [12]:
forward_rate_cub_coef = interpolate.CubicSpline(maturity, forward_rate)
forward_rate_cub = forward_rate_cub_coef(new_mat)

In [13]:
fig = make_subplots(rows=3, cols=1, subplot_titles=("Yield Curve", "Forward Rate"))
fig.append_trace(go.Scatter(x=y_to_maturity_arr, y=yield_arr, mode='markers', name='Yield Curve'), row=1, col=1)
fig.append_trace(go.Scatter(x=new_mat, y=new_yield, mode='lines', name='Nelson-Siegel (ns)'), row=1, col=1)
fig.append_trace(go.Scatter(x=new_mat, y=yield_fit_cub, mode='lines', name='Cubic Spline'), row=1, col=1)
fig.append_trace(go.Scatter(x=new_mat, y=new_yield_nss, mode='lines', name='Nelson-Siegel (nss)'), row=1, col=1)
fig.append_trace(go.Scatter(x=new_mat, y=yield_fit_hcub, mode='lines', name='Cubic Hermite Spline'), row=1, col=1)
fig.append_trace(go.Scatter(x=maturity, y=forward_rate, mode='markers', name='Forward Rate'), row=2, col=1)
fig.append_trace(go.Scatter(x=new_mat, y=new_forward, mode='lines', name='Nelson-Siegel (nss)'), row=2, col=1)
# fig.append_trace(go.Scatter(x=new_mat, y=new_forward_ns, mode='lines', name='Nelson-Siegel (ns)'), row=2, col=1)
fig.append_trace(go.Scatter(x=new_mat, y=forward_rate_cub, mode='lines', name='Cubic Spline'), row=2, col=1)
fig.append_trace(go.Scatter(x=new_mat, y=forward_fit_hcub, mode='lines', name='Cubic Hermite Spline'), row=2, col=1)
fig.append_trace(go.Scatter(x=y_to_maturity_arr, y=yield_arr, mode='markers', name='yield'), row=3, col=1)
fig.append_trace(go.Scatter(x=y_to_maturity_arr, y=forward_rate, mode='markers', name='Forward'), row=3, col=1)
fig.update_layout(title='Yield Curve Interpolation')
fig.show()

In [17]:
a = np.arange(16).reshape(4, 4)
a

array([[ 0,  1,  2,  3],
       [ 4,  5,  6,  7],
       [ 8,  9, 10, 11],
       [12, 13, 14, 15]])

In [18]:
a.diagonal()

array([ 0,  5, 10, 15])

In [22]:
swaption_iv = pd.read_csv(r"C:\Users\rrenard\OneDrive - Arkus\Desktop\swapIV.csv", index_col=0)

In [27]:
swaption_iv

1Yr    2Yr    3Yr    4Yr    5Yr    7Yr   10Yr   12Yr   15Yr   20Yr  \
Expiry                                                                         
1Yr     27.20  27.65  27.50  27.18  26.72  25.82  24.73  24.28  23.63  22.97   
2Yr     29.56  28.85  28.36  27.81  27.09  26.05  24.87  24.37  23.76  23.20   
3Yr     29.80  28.68  27.88  27.31  26.69  25.70  24.52  24.04  23.51  23.12   
4Yr     29.01  27.84  27.08  26.53  25.99  25.03  23.94  23.56  23.06  22.83   
5Yr     27.78  26.75  26.10  25.63  25.19  24.30  23.36  23.09  22.59  22.57   
7Yr     25.93  25.05  24.55  24.02  23.57  22.91  22.28  22.01  21.83  22.02   
10Yr    23.37  22.82  22.27  21.86  21.40  21.17  20.66  20.79  20.70  21.10   
12Yr    22.17  21.67  21.21  21.08  20.84  20.51  20.41  20.47  20.53  21.08   
15Yr    21.65  21.19  20.80  20.46  20.13  20.37  20.19  20.40  20.44  21.26   
20Yr    22.95  22.38  21.93  21.52  21.11  21.29  20.87  21.37  21.74  22.25   
25Yr    25.86  25.13  24.56  24.01  23.48  24.20  24.01  24.19  24.22  26.61   
30Yr    31.75  31.82  31.21  30.37  29.53  28.36  26.26  27.75  29.38  31.43   

         25Yr   30Yr  
Expiry                
1Yr     23.12  23.41  
2Yr     23.36  23.76  
3Yr     23.33  23.82  
4Yr     23.12  23.71  
5Yr     22.92  23.61  
7Yr     22.55  23.22  
10Yr    21.89  22.56  
12Yr    21.82  22.74  
15Yr    21.92  23.38  
20Yr    23.95  25.39  
25Yr    28.58  30.06  
30Yr    33.01  34.17

In [24]:
swaption_iv_arr = np.array(swaption_iv)

In [29]:
iv_diag = swaption_iv_arr.diagonal()/100

In [30]:
import QuantLib as ql

In [32]:
def CreateSwaptionVolatilityList(vol: np.ndarray):
    vol_list = []
    for item in vol:
        vol_list.append(item)
    return vol_list

In [33]:
swaption_iv_list = CreateSwaptionVolatilityList(iv_diag)

In [36]:
class ModelCalibrator:
    def __init__(self, endCriteria):
        self.endCriteria = endCriteria
        self.helpers = []

    def AddCalibrationHelper(self, helper):
        self.helpers.append(helper)

    def Calibrate(self, model, engine, curve, fixedParameters):
        # assign pricing engine to all calibration helpers
        for i in range(len(self.helpers)):
            self.helpers[i].setPricingEngine(engine)
        method = ql.LevenbergMarquardt()
        if len(fixedParameters) == 0:
            model.calibrate(self.helpers, method, self.endCriteria)
        else:
            model.calibrate(
                self.helpers,
                method,
                self.endCriteria,
                ql.NoConstraint(),
                [],
                fixedParameters,
            )

In [37]:
# general parameters
tradeDate = ql.Date(24, ql.May, 2024)
ql.Settings.instance().evaluationDate = tradeDate
calendar = ql.TARGET()
dayCounter = ql.Actual360()

In [38]:
matruity_dates_ql = [
    ql.Date(data["MarketDate"][0], "%Y-%m-%d") + int(d)
    for d in data["DaysToMaturity"]
]
maturity_array = np.array(matruity_dates_ql)

In [42]:
maturity_array.shape, forward_rate.shape

((55,), (55,))

In [43]:
ts = ql.ForwardCurve(maturity_array, forward_rate, ql.Actual360())
ts_handle = ql.YieldTermStructureHandle(ts)

In [44]:
# create calibrator object
endCriteria = ql.EndCriteria(10000, 100, 0.000001, 0.00000001, 0.00000001)
calibrator = ModelCalibrator(endCriteria)

In [45]:
# add swaption helpers to calibrator
for i in range(len(swaption_iv_list)):
    t = i + 1
    tenor = len(swaption_iv_list) - i
    helper = ql.SwaptionHelper(
        ql.Period(t, ql.Years),
        ql.Period(tenor, ql.Years),
        ql.QuoteHandle(ql.SimpleQuote(swaption_iv_list[i])),
        ql.USDLibor(ql.Period(3, ql.Months), ts_handle),
        ql.Period(1, ql.Years),
        dayCounter,
        dayCounter,
        ts_handle,
    )
    calibrator.AddCalibrationHelper(helper)


In [47]:
print("case 1 : calibrate all involved parameters (HW1F : reversion, sigma)")
model = ql.HullWhite(ts_handle)
engine = ql.JamshidianSwaptionEngine(model)
fixedParameters = []
calibrator.Calibrate(model, engine, ts_handle, fixedParameters)
print("calibrated reversion: " + str(round(model.params()[0], 5)))
print("calibrated sigma: " + str(round(model.params()[1], 5)))
print()

case 1 : calibrate all involved parameters (HW1F : reversion, sigma)
calibrated reversion: 0.24642
calibrated sigma: 0.0225

